In [ ]:
%matplotlib inline


# Jacobi MDA

A smart MDA that solves only strongly coupled disciplines
and then executes the weakly coupled ones


In [ ]:
from __future__ import annotations

from os import name as os_name

from gemseo.api import configure_logger
from gemseo.api import create_discipline
from gemseo.api import create_mda

IS_NT = os_name == "nt"

configure_logger()

## Define a way to display results



In [ ]:
def display_result(res, mda_name):
    """Display coupling and output variables in logger.

    @param res: result (dict) of MDA
    @param mda_name: name of the current MDA
    """
    # names of the coupling variables
    coupling_names = [
        "y_11",
        "y_12",
        "y_14",
        "y_21",
        "y_23",
        "y_24",
        "y_31",
        "y_32",
        "y_34",
    ]
    for coupling_var in coupling_names:
        print(
            "{}, coupling variable {}: {}".format(
                mda_name, coupling_var, res[coupling_var]
            ),
        )

    # names of the output variables
    output_names = ["y_1", "y_2", "y_3", "y_4", "g_1", "g_2", "g_3"]
    for output_name in output_names:
        print(
            f"{mda_name}, output variable {output_name}: {res[output_name]}",
        )

## Create, execute and post-process MDA
We do not need to specify the inputs, the default inputs
of the MDA will be used and computed from the
Default inputs of the disciplines



In [ ]:
disciplines = create_discipline(
    [
        "SobieskiStructure",
        "SobieskiPropulsion",
        "SobieskiAerodynamics",
        "SobieskiMission",
    ]
)
use_threading = False
if IS_NT:
    use_threading = True
mda = create_mda(
    "MDAJacobi",
    disciplines,
    acceleration="m2d",
    warm_start=True,
    n_processes=4,
    use_threading=use_threading,
)
res = mda.execute()
display_result(res, mda.name)
mda.plot_residual_history(
    n_iterations=10,
    logscale=[1e-8, 10.0],
    save=False,
    show=True,
    fig_size=(10, 2),
)